<span style="font-size:8pt">*ENSAM-Bordeaux, Mathématiques et informatique. Date : le 04/11/19. Auteur : Éric Ducasse. Version : 1.1*</span>

<div class="alert alert-block alert-danger"> <span style="color:#800000"> *On pourra faire exécuter ce notebook cellule par cellule $\left(\mathtt{Maj+Entrée}\right)$ ou intégralement par $\mathtt{\;Kernel\rightarrow Restart\;\&\;Run\;All}$.* </span> </div>

In [ ]:
%matplotlib inline

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

In [ ]:
import sympy as sb
sb.init_printing()

In [ ]:
print(f"Version de sympy : {sb.__version__}") 

# <span style="color:#0066BB"> **Calcul formel : TD n°2, seconde partie** </span>

<div class="alert alert-block alert-danger"> <span style="color:#800000"> **Pour chaque exercice, faire exécuter la partie *exemples* cellule par cellule $\left(\mathtt{Maj+Entrée}\right)$, avant de passer à la partie *Travail à faire*.** </span> </div>

## <span style="color: #0000BB"> *Exercice 12* </span>

### <span style="color:purple"> 12.1 Objectifs </span>

####  *<span style="color:#005500"> Savoir définir et résoudre un système d'équations algébriques, en utilisant la fonction $\mathtt{sympy.solve}$;<br /> savoir utiliser le résultat d’un calcul symbolique pour créer une fonction, en maîtrisant la fonction $\mathtt{sympy.lambdify}$. </span>*

Documentation sur les équations et les solveurs :<br />https://docs.sympy.org/latest/tutorial/solvers.html

Documentation sur $\mathtt{lambdify}$ :<br />https://docs.sympy.org/latest/tutorial/basic_operations.html#lambdify

### <span style="color:purple"> 12.2 Exemples </span>

#### Problème à résoudre : déterminer les paramètres $a$ et $b$ d'une fonction paramétrée pour satisfaire des conditions initiales données.

<span style="color:#006020">*$a)$ Définition d'une expression représentant une fonction de la variable $t$ avec 4 paramètres $a$, $b$, $\omega$ et $\tau$.*</span>

In [ ]:
a,b,t = sb.symbols("a,b,t", real=True)
w,tau = sb.symbols("omega,tau", positive=True)
U_de_t = (a*sb.cos(w*t)+b*sb.sin(w*t))*sb.exp(-t/tau)
U_de_t

<span style="color:#006020">*$b)$ Valeurs initiales de la fonction et de sa dérivée.*</span>

In [ ]:
valeur_initiale = U_de_t.replace(t,0) ; valeur_initiale

In [ ]:
derivee_initiale = U_de_t.diff(t).replace(t,0) ; derivee_initiale

<span style="color:#006020">*$c)$ Détermination des paramètres $a$ et $b$ qui permettent à la fonction de satisfaire des conditions initiales données.*</span>

In [ ]:
u0,v0 = sb.symbols("u_0,v_0")
equations = [sb.Eq(valeur_initiale,u0), sb.Eq(derivee_initiale,v0)]
equations

In [ ]:
regle_ab = sb.solve(equations, [a,b]) ; regle_ab

* Variante, sans utiliser d'équation :

In [ ]:
s_annulent = [valeur_initiale-u0, derivee_initiale-v0]
s_annulent

In [ ]:
sb.solve(s_annulent, [a,b])

<span style="color:#006020">*$d)$ Solution du problème.*</span>

In [ ]:
solu = U_de_t.xreplace(regle_ab).simplify()
solu

<span style="color:#006020">*$e)$ Définition de fonctions utilisant le dernier résultat.*</span>

La fonction $\mathtt{lambdify}$ est faite pour définir une fonction à valeurs numériques :

In [ ]:
print(sb.lambdify.__doc__[:487])

* <span style="color:#0050A0">**Fonction à valeurs symboliques : on utilise $\mathtt{xreplace}$**</span>

In [ ]:
alpha,f = sb.symbols("alpha,f", positive=True)
solu.xreplace({tau:1/alpha, w:2*sb.pi*f}).simplify()

In [ ]:
def Us(time,initial_value=1,initial_derivative=0,frequency=1,time_constant=1,expression=solu) : 
    regle = {u0:initial_value, v0:initial_derivative, w:sb.pi*2*frequency, tau:time_constant}
    return expression.xreplace(regle).simplify()
# Remarque : on peut aussi définir une fonction lambda, avec des performances identiques
Us(t)

In [ ]:
Us(t,frequency=f,time_constant=1/alpha,initial_value=0,initial_derivative=1)

* <span style="color:#0050A0">**Fonction vectorisée à valeurs numériques**</span>

Avec $\mathtt{lambdify}$, on ne peut pas définir de valeurs par défaut.
Si on veut le faire, il faut procéder en deux temps, comme ci-dessous.

In [ ]:
u_numerique = sb.lambdify( (t,u0,v0,w,tau), solu, "numpy")

In [ ]:
T = np.arange(0,1.01,0.2)
print(np.array( [T,u_numerique(T,1,0,2*np.pi,1)] ))

In [ ]:
Un = lambda t,u0=1,v0=0,w=2*np.pi,tau=1 : u_numerique(t,u0,v0,w,tau)
print(np.array( [T,Un(T)] ))

In [ ]:
Vt = np.linspace(0,3.2,500)
plt.plot(Vt,Un(Vt),"-r",linewidth=1.6,label=r"$f$ = 1 Hz ; $\tau$ = 1 s")
for fq,ct in ((1,2),(2,1)) :
    plt.plot(Vt,Un(Vt,w=2*np.pi*fq,tau=ct),"-",linewidth=1.6,\
             label=r"$f$ = {} Hz ; $\tau$ = {} s".format(fq,ct))
plt.grid() ; plt.legend() ; plt.xlabel("Temps $t$ [s]") ; plt.ylabel("$u(t)$") ;

### <span style="color:purple"> 12.3 Travail à faire </span>

L'objet de cet exercice est de définir 4 fonctions $p$ polynomiales de degré 3, que l'on considère uniquement sur l'intervalle $[0,1]$ telles que l'une des valeurs parmi $[p(0),p^{\prime}(0),p(1),p^{\prime}(1)]$ est 1 et les trois autres sont 0.

$a)$ Soit l'expression $P=p(X)=a+b\,X+c\,X^2+d\,X^3$. Déterminer la liste $[p(0),p^{\prime}(0),p(1),p^{\prime}(1)]$ en fonction des paramètres $a$, $b$, $c$ et $d$.

In [ ]:
a,b,c,d,X = sb.symbols("a,b,c,d,X")
P = ( a + X*(b + X*(c + X*d))).expand(); P

In [ ]:
valeurs_limites = [P.replace(X,0), P.diff(X).replace(X,0), P.replace(X,1), P.diff(X).replace(X,1)]
valeurs_limites

$b)$ En déduire les expressions correspondants aux 4 fonctions cherchées.

In [ ]:
from IPython.display import display
expr = []
for p0,q0,p1,q1 in np.eye(4, dtype=np.int) :
    print(f"+++ p(0)={p0}, p'(0)={q0}, p(1)={p1}, p'(1)={q1} +++") 
    equations = [ sb.Eq(p,v) for p,v in zip((p0,q0,p1,q1),valeurs_limites) ]
    display(equations)
    regle_abcd = sb.solve(equations,(a,b,c,d))
    display(regle_abcd)
    expr.append( P.xreplace(regle_abcd).simplify() )
    display(expr[-1])
    

$c)$ Convertir ces expressions en 4 fonctions numériques et faire tracer leurs courbes représentatives sur l'intervalle $[0,1]$.

In [ ]:
LF = [ sb.lambdify(X,E,"numpy") for E in  expr ]
LF

In [ ]:
Vx = np.linspace(0,1,200)
for n,f in enumerate(LF,1) :
    plt.plot(Vx,f(Vx),"-",linewidth=2.0, label=f"$p_{n}(x)$")
plt.grid() ; plt.legend(loc="best") ; plt.xlabel("$x$") ; plt.ylabel("$p(x)$") ;

## <span style="color: #0000BB"> *Exercice 13* </span>

### <span style="color:purple"> 13.1 Travail à faire </span>

On s'intéresse à la solution $f$ du système différentiel $(1)$ suivant : $\displaystyle \left\lbrace\begin{array}{lll} \forall r\in]0,2], & \displaystyle f^{\prime\prime}(r)+\frac{1}{r}\,f^{\prime}(r)+25\,f(r)=0&; \\ \forall r\in]2,5[ & 
\displaystyle f^{\prime\prime}(r)+\frac{1}{r}\,f^{\prime}(r)+4\,f(r)=0&.\end{array}\right.$<br />la solution $f$ étant de classe $\mathcal{C}^{1}$ sur l'intervalle $[0,5]$ et vérifiant les conditions aux limites : $f^{\prime}(0)=0$ et $f(5)=1$.

On admet que la solution générale de l'équation différentielle $\displaystyle f^{\prime\prime}(r)+\frac{1}{r}\,f^{\prime}(r)+k^2\,f(r)=0$ est une combinaison linéaire des deux fonctions $r\mapsto J_0(k\,r)$ et
$r\mapsto Y_0(k\,r)$, où $J_0$ et $Y_0$ désignent les fonctions de Bessel de première et de seconde espèces :

In [ ]:
r,k = sb.symbols("r,k", real=True, nonnegative=True)
S1,S2 = sb.besselj(0,k*r),sb.bessely(0,k*r)
(S1,S2)

In [ ]:
[ (S.diff(r,2) + (1/r)*S.diff(r) + k**2*S ).equals(0) for S in (S1,S2) ]

L'étude de ces deux fonctions en $r=0$ donne les résultats suivants :

In [ ]:
S1.replace(r,0), S1.diff(r).replace(r,0), S2.limit(r,0)

On en déduit la solution générale du problème différentiel :

* Sur l'intervalle $[0,2]$ :

In [ ]:
a,b,c = sb.symbols("a,b,c", real=True)
F1 = a*sb.besselj(0,5*r) ; F1

* Sur l'intervalle $[2,5]$ :

In [ ]:
F2 = b*sb.besselj(0,2*r)+c*sb.bessely(0,2*r) ; F2

$a)$ Vérifier que la solution proposée satisfait bien la condition limite à gauche. Définir ensuite un système de 3 équations à 3 inconnues $a$, $b$ et $c$ à partir des conditions de raccordement en $r=2$ de la fonction et de sa dérivée, et de la condition limite à droite.

In [ ]:
sb.Eq(F1.diff(r).replace(r,0),0)

In [ ]:
systeme = [ sb.Eq(F1,F2).replace(r,2), \
            sb.Eq(F1.diff(r),F2.diff(r)).replace(r,2), \
            sb.Eq(F2.replace(r,5),1) ]
systeme

$b)$ En déduire les coefficients $a$, $b$ et $c$ qui satisfont le problème différentiel $(1)$, puis la solution sur chacun des intervalles $[0,2]$ et $[2,5]$.

In [ ]:
regle_abc = sb.solve(systeme, (a,b,c)) ; regle_abc

In [ ]:
F_sol1 = F1.xreplace(regle_abc).simplify() ; F_sol1

In [ ]:
F_sol2 = F2.xreplace(regle_abc).simplify() ; F_sol2

$c)$ Définir la solution sous forme d'une fonction numérique vectorisée $\mathtt{f\underline{\phantom{m}}num}$ puis faire tracer sa courbe représentative. Les fonctions de Bessel numériques se trouvent dans le module $\mathtt{scipy.special}$ et se nomment $\mathtt{jn}$ et $\mathtt{yn}$.

In [ ]:
import scipy.special as sf

In [ ]:
mes_modules = ["numpy",{"besselj":sf.jn, "bessely":sf.yn}]
F_num1 = sb.lambdify( r, F_sol1, modules=mes_modules )
F_num2 = sb.lambdify( r, F_sol2, modules=mes_modules )

In [ ]:
F_num_brouillon = lambda r : ((0<=r)&(r<=2))*F_num1(r) + ((2<r)&(r<=5))*F_num2(r)
F_num_brouillon(np.linspace(0,5,11))

In [ ]:
print(f"Le problème en 0 vient du calcul de F_num2(0) : {F_num2(0)}.\n" + \
       "Pour régler ce problème, ou peut utiliser numpy.clip(a, a_min, a_max) :\n", \
       np.clip.__doc__[:866])

In [ ]:
F_num = lambda r : ((0<=r)&(r<=2))*F_num1(np.clip(r,0,2)) + ((2<r)&(r<=5))*F_num2(np.clip(r,2,5))
F_num(np.linspace(0,5,11))

In [ ]:
R = np.linspace(0,5,200)
plt.plot(R,F_num(R),"m-")
plt.grid() ;

# <span style="color:#0066BB"> **Compléments non exigibles** </span>

## <span style="color: #0000BB"> *Exercice 12 : compléments sur $\mathtt{lambdify}$* </span>

### <span style="color:purple"> 12.2 Exemples complémentaires </span>

<span style="color:#006020">*$f)$ Autres exemples avec des fonctions qui ne sont pas dans $\mathtt{numpy}$ (voir aussi le mémento).*</span>

* <span style="color:#0050A0">**Fonction $\mathtt{sympy.erfc}$**</span>

In [ ]:
x,t = sb.symbols("x,t", real=True)
Ix = sb.integrate( sb.exp(-t**2), (t,x,sb.oo) ).rewrite(sb.erfc).simplify()
Ix

In [ ]:
try :
    F = sb.lambdify( x, Ix, modules=["numpy"])
    F( np.array([0.2,0.4]) )
except Exception as e :
    print("Erreur :",e)

In [ ]:
print(sb.erfc.__doc__[:161])

In [ ]:
import scipy.special as sf # Special Functions
print(sf.erfc.__doc__[:168])

In [ ]:
# Vérification :
T = np.linspace(0,2.5,100)
V1 = sf.erfc(T)
V2 = np.array( [float(sb.erfc(x)) for x in T] )
np.allclose(V1,V2)

In [ ]:
plt.plot(T,V1-V2,".m") ; plt.grid() ;

In [ ]:
F = sb.lambdify( x, Ix, modules=[{"erfc":sf.erfc}, "numpy"])
F( np.array([0.2,0.4]) )

In [ ]:
plt.plot(T,F(T),"-g") ; plt.grid() ; plt.xlabel("$t$") ; plt.ylabel("$F(t)$") ; 

* <span style="color:#0050A0">**Fonction $\mathtt{sympy.lowergamma}$**</span>

In [ ]:
x,t = sb.symbols("x,t", positive=True)
Jx = sb.integrate( sb.sqrt(t)*sb.exp(-t**2), (t,0,x) ).simplify()
Jx

In [ ]:
try :
    G = sb.lambdify( x, Jx, modules=["numpy"])
    G( np.array([0.2,0.4]) )
except Exception as e :
    print("Erreur :",e)

In [ ]:
print(sb.lowergamma.__doc__[:202])

In [ ]:
print(sf.gammainc.__doc__[:259])

In [ ]:
def my_lowergamma(s,x) :
    return sf.gamma(s)*sf.gammainc(s,x)
T = np.linspace(0,2.5,100)
W1 = my_lowergamma(0.75,T) ; W1[:5]

In [ ]:
W2 = np.array([ float(sb.lowergamma(0.75,x)) for x in T ]) ; W2[:5]

In [ ]:
np.allclose(W1,W2)

In [ ]:
G = sb.lambdify( x, Jx, modules=[{"lowergamma":my_lowergamma},"numpy"])
G( np.array([0.2,0.4]) )

In [ ]:
plt.plot(T,G(T),"-r") ; plt.grid() ; plt.xlabel("$t$") ; plt.ylabel("$G(t)$") ; 

In [ ]:
#Variante :
G_bis = sb.lambdify( x, Jx, modules=[{"lowergamma": lambda s,x : sf.gamma(s)*sf.gammainc(s,x)},"numpy"])
G_bis( np.array([0.2,0.4]) )

In [ ]:
np.allclose(G(T),G_bis(T))